# Affordability of Living in Florida by County

## **1 Summary**

For each County in the State of Florida, I created a map that will color code based on Income/cost-of-living ratio; from red, to yellow, to green from least to most livable for a given family size and Income.

## **2 Motivation**

I'm always interest in using the tools at our disposal to improve as many lives as possible; this data is valuable for us to gain an understanding of how much strain is put on a person, or a family, depending on where they live.

## **3 Skills and Tools Used**

### **3.1 Skills**

<ul>
  <li>Python
    <ul>
      <li>Data Analysis</li>
      <li>Data Cleaning</li>
      <li>Data Visualization</li>
      <li>Project Documentation</li> 
    </ul>
  </li>
  <li>Jupyter Notebooks</li>
</ul> 

### **3.2 Tools**

<ul>
  <li>Python
    <ul>
      <li>pandas</li>
      <li>geopandas</li>
      <li>folium</li>
      <li>numpy</li> 
    </ul>
  </li>
  <li>Jupyter Notebooks</li>
</ul> 

## **4 My Aim and our Limitations**

The Economic Policy Institute collects cost-of-living data for every county in the United States. The data includes cost of housing, food, child care, transportation, health care, other necessities, and taxes for family types ranging from a single person (1p0c) up to two adults and four children (2p4c). On the EPIs website you can browse a choropleth map showing cost of living for a two-parent, two-child family for the US, you can get a fact sheet breakdown per county of these costs, or you can get a similar breakdown of costs and compare between family types and counties. What I wanted was a mix of the three; a way to customize the choropleth with your own personal information and get a visual indicator of how your family would fare across the literal map. 

#### Map on the EPI Website.


![EPI Map](https://www.epi.org/files/2018/familybudget-map-mini-2018.png)

### **4.1 Things this data can tell us**

    How does cost of living in one county compare to another?
    How much would someone earning X dollars do in each county?
    What is the median Income in each county?
    How well does a single person do vs a couple vs a family?

### **4.2 Things this data can't tell us**

    *Why* different areas have different income or cost-of-living.
    What people do for work in each county.
    Where people work compared to where they live.

## **5 Dataset Selection**

We are using cost of living data from Economic Policy Institute and location data from the United States Census Bureau

## **6 Data Preparation**

    6.1 US Census Data
    6.2 EPI Data
    6.3 Combining the Data

**6.1 US Census Data**

First we are loading in the shapefile from the US Census Bureau and checking for missing data.

In [25]:
import pandas as pd
import geopandas as gpd
from openpyxl import Workbook

# Step 1: Load the shapefile using GeoPandas
shapefile_path = "florida_counties.geojson"
gdf = gpd.read_file(shapefile_path)

# Print the dimensions of the DataFrame, check for missing values, and display the first five rows and columns
print("Number of rows: ", gdf.shape[0], "\nNumber of columns: ", gdf.shape[1])
print("Contains missing values:", gdf.isnull().values.any())
print("First five rows and columns:")
gdf.iloc[:5,:5]

Number of rows:  83 
Number of columns:  19
Contains missing values: True
First five rows and columns:


STATEFP COUNTYFP  COUNTYNS  GEOID         GEOIDFQ
0      12      087  00295759  12087  0500000US12087
1      12      086  00295755  12086  0500000US12086
2      12      011  00295753  12011  0500000US12011
3      12      021  00295754  12021  0500000US12021
4      12      071  00295758  12071  0500000US12071

In [6]:
gdf.isna().sum()

STATEFP        0
COUNTYFP       0
COUNTYNS       0
GEOID          0
GEOIDFQ        0
NAME           0
NAMELSAD       0
LSAD           0
CLASSFP        0
MTFCC          0
CSAFP       1894
CBSAFP      1320
METDIVFP    3096
FUNCSTAT       0
ALAND          0
AWATER         0
INTPTLAT       0
INTPTLON       0
geometry       0
dtype: int64

A shapefile is a file type that contains geographic and cartographic information. The shapefile being used here is the 2023 county Tiger/Line shapefile provided by he United States Census Bureau. This and other very interesting data can be found at the census website. This shapefile will have the latitudinal and longitudinal dimensions of the counties we are looking at.

The parts of the geodataframe we care about are the STATEFP. NAME, and geometry columns. Our missing data columns aren't necessary. 

For this project, I wanted to keep the scope small, so I focused on just one state. I could probably expand to a tri-state model, or simply let the user select the state that they want to see data for in the future. I wanted to search the data for a way to exclude any columns that don't include Florida-based counties.

County Geographic Data: https://data.census.gov/

In [7]:
# Looking for a field to distinguish Florida counties
gdf_florida = gdf[gdf['NAME'] == 'Pinellas']
gdf_florida

STATEFP COUNTYFP  COUNTYNS  GEOID         GEOIDFQ      NAME  \
927      12      103  00295745  12103  0500000US12103  Pinellas   

            NAMELSAD LSAD CLASSFP  MTFCC CSAFP CBSAFP METDIVFP FUNCSTAT  \
927  Pinellas County   06      H1  G4020  None  45300    41304        A   

         ALAND      AWATER     INTPTLAT      INTPTLON  \
927  709091780  1535981840  +27.9053425  -082.7980663   

                                              geometry  
927  POLYGON ((-83.01875 28.17098, -82.95907 28.171...

The "FP" part of STATEFP and COUNTYFP is short for the Federal Information Processing Standards (FIPS) code, which are used to uniquely identify geographic regions. States are two digits; counties are five digits with the first two belonging to the corresponding state. For example, the FIPS code for Pinellas County, FL is 12103.

I grew up in Pinellas County, FL. This happens to be a unique county name in the US. From the STATEFP column we can see that Floridian counties will be under STATEFP 12.

In [8]:
# Our data designates Florida as 12. We will only include Florida shapes
florida_boundary = gdf[gdf['STATEFP'] == '12']
gdf_clipped = gpd.clip(gdf,florida_boundary)

**6.2 EPI Data**

The Economic Policy Institute collects cost-of-living data for every county in the United States. The data includes cost of housing, food, child care, transportation, health care, other necessities, and taxes for family types ranging from a single person (1p0c) up to two adults and four children (2p4c). On the EPIs website you can browse a choropleth map showing cost of living for a two-parent, two-child family for the US, you can get a fact sheet breakdown per county of these costs, or you can get a similar breakdown of costs and compare between family types and counties. What I wanted was a mix of the three; a way to customize the choropleth with your own personal information and get a visual indicator of how your family would fare across the literal map.

Cost of Living Data: https://www.epi.org/publication/family-budget-calculator-documentation/

In [9]:
#Reading in our cost of living data
cost_of_living_data_path = "fbc_data_2024.xlsx"
cost_of_living_data = pd.read_excel(cost_of_living_data_path,sheet_name="County")

In [10]:
cost_of_living_data.head()

case_id State abv.  county_fips          County Family  Housing   Food  \
0        1         AL         1001  Autauga County   1p0c     9804   4020   
1        1         AL         1001  Autauga County   1p1c    13368   5928   
2        1         AL         1001  Autauga County   1p2c    13368   8676   
3        1         AL         1001  Autauga County   1p3c    16992  11592   
4        1         AL         1001  Autauga County   1p4c    16992  14184   

   Transportation  Healthcare  Other Necessities   ...   Total  \
0           13320        6120                4896  ...   45636   
1           16380        9072                6840  ...   66960   
2           18840       12036                7812  ...   84252   
3           20040       14988               10116  ...  102492   
4           20904       17940               11040  ...  112704   

   median_family_income  num_counties_in_st  st_cost_rank  st_med_aff_rank  \
0               83790.0                  67             8               58   
1               83790.0                  67             8               58   
2               83790.0                  67             8               58   
3               83790.0                  67             8               58   
4               83790.0                  67             8               58   

   st_income_rank  Total_minus_Transport  Transportation_base  \
0             7.0                  32316                 3330   
1             7.0                  50580                 4095   
2             7.0                  65412                 4710   
3             7.0                  82452                 5010   
4             7.0                  91800                 5226   

   Transportation_per_day  county_fip_last_three_digits  
0                  1998.0                             1  
1                  2457.0                             1  
2                  2826.0                             1  
3                  3006.0                             1  
4                  3135.6                             1  

[5 rows x 22 columns]

In [11]:
# Print the dimensions of the DataFrame, check for missing values, and display the first five rows and columns
print("Number of rows: ", cost_of_living_data.shape[0], "\nNumber of columns: ", cost_of_living_data.shape[1])
print("Contains missing values:", cost_of_living_data.isnull().values.any())
print("First five rows and columns:")
cost_of_living_data.iloc[:5,:5]

Number of rows:  31430 
Number of columns:  22
Contains missing values: True
First five rows and columns:


case_id State abv.  county_fips          County Family
0        1         AL         1001  Autauga County   1p0c
1        1         AL         1001  Autauga County   1p1c
2        1         AL         1001  Autauga County   1p2c
3        1         AL         1001  Autauga County   1p3c
4        1         AL         1001  Autauga County   1p4c

In [12]:
cost_of_living_data.isna().sum()

case_id                          0
State abv.                       0
county_fips                      0
County                           0
Family                           0
Housing                          0
Food                             0
Transportation                   0
Healthcare                       0
Other Necessities                0
Childcare                        0
Taxes                            0
Total                            0
median_family_income            10
num_counties_in_st               0
st_cost_rank                     0
st_med_aff_rank                  0
st_income_rank                   0
Total_minus_Transport            0
Transportation_base              0
Transportation_per_day           0
county_fip_last_three_digits     0
dtype: int64

In [13]:
cost_of_living_data[cost_of_living_data['median_family_income'].isna()]

case_id State abv.  county_fips           County Family  Housing  \
15110     1512         MO        29055  Crawford County   1p0c     6012   
15111     1512         MO        29055  Crawford County   1p1c     9000   
15112     1512         MO        29055  Crawford County   1p2c     9000   
15113     1512         MO        29055  Crawford County   1p3c    12024   
15114     1512         MO        29055  Crawford County   1p4c    12024   
15115     1512         MO        29055  Crawford County   2p0c     6876   
15116     1512         MO        29055  Crawford County   2p1c     9000   
15117     1512         MO        29055  Crawford County   2p2c     9000   
15118     1512         MO        29055  Crawford County   2p3c    12024   
15119     1512         MO        29055  Crawford County   2p4c    12024   

        Food  Transportation  Healthcare  Other Necessities   ...   Total  \
15110   3780           13620        6060                3468  ...   38820   
15111   5568           16476        9480                5160  ...   56784   
15112   8148           18144       12912                6072  ...   71340   
15113  10884           19356       16344                8112  ...   88116   
15114  13320           21084       19776                8976  ...  100092   
15115   6924           15744       12108                4884  ...   53316   
15116   8616           17292       15540                6240  ...   69192   
15117  10908           18420       18972                7044  ...   82416   
15118  13320           20088       22404                8976  ...   98112   
15119  16308           20784       25836               10032  ...  109032   

       median_family_income  num_counties_in_st  st_cost_rank  \
15110                   NaN                 115           102   
15111                   NaN                 115           102   
15112                   NaN                 115           102   
15113                   NaN                 115           102   
15114                   NaN                 115           102   
15115                   NaN                 115           102   
15116                   NaN                 115           102   
15117                   NaN                 115           102   
15118                   NaN                 115           102   
15119                   NaN                 115           102   

       st_med_aff_rank  st_income_rank  Total_minus_Transport  \
15110               55            78.0                  25200   
15111               55            78.0                  40308   
15112               55            78.0                  53196   
15113               55            78.0                  68760   
15114               55            78.0                  79008   
15115               55            78.0                  37572   
15116               55            78.0                  51900   
15117               55            78.0                  63996   
15118               55            78.0                  78024   
15119               55            78.0                  88248   

       Transportation_base  Transportation_per_day  \
15110                 3405                  2043.0   
15111                 4119                  2471.4   
15112                 4536                  2721.6   
15113                 4839                  2903.4   
15114                 5271                  3162.6   
15115                 3936                  2361.6   
15116                 4323                  2593.8   
15117                 4605                  2763.0   
15118                 5022                  3013.2   
15119                 5196                  3117.6   

       county_fip_last_three_digits  
15110                            55  
15111                            55  
15112                            55  
15113                            55  
15114                            55  
15115                            55  
15116                            55  
15

We have ten records with missing Median family income for the state of Missouri. Since I am focusing on Florida I'm dropping the rows for these records anyway. If I were to keep these records or adjust my code to work with any state I probably wouldn't simply drop the entire records. We could flag these records as missing the data, or, possibly, try to impute the values and make clear this is an estimate of my own. Either way we are moving on.

In [14]:
# Keeping only Florida
cost_of_living_data_clipped = cost_of_living_data[cost_of_living_data['State abv.'] == 'FL']
cost_of_living_data_clipped = cost_of_living_data[cost_of_living_data['State abv.'] == 'FL']

**6.3 Combining the Data**

My original idea of this project was very different. I wanted to do a "livability index" that took crime and cost-of-living into account, possibly even other factors like how many days a week the user planned to commute to calculate wear and tear of their vehicle. The original idea was to let someone take as many factors as possible of a given place in in order to decide where they want to live. While I think the idea has merit as a possible political tool there were two large problems. 

1. Including crime in any sort of analysis is always going to be arbitrary and will have to include caveats.
2. For someone who is interested in where to live giving information outside of hard costs is needlessly confusing. People already know where they want to live, what kind of places appeal to them. They care more about being close to friends and family than anything else, money being a close second.

So, I cut the crime angle and other planned features. My original idea was to create an app out of this idea, the scope seemed small enough that this would be a good first practice case. I worked for nearly four months after getting a working prototype of my original idea before I realized that this was a poorly thought out idea and taking more time on it would hurt more than help. I still have the code for a failed application deployed via Streamlit that ran way too slowly to ever be of practical use. I may switch to another library and take another shot one day if the EPI doesn't implement my idea in the way that I wanted to see it. 

Another legacy of the application version of this project; affordability ratios are precalculated. Because the Streamlit library runs all code from top to bottom at the slightest user input, dynamically calculated Income/cost of living ratios made trying to use the map glacial. To work around this, I chose to precalculate these values for income levels up to \\$200,000 (in \\$10,000 increments) across all counties and family sizes and stuck with that solution when I dropped the app idea. Precomputing the values increased the dataset size, but the benefit of eliminating real-time calculations outweighed the cost for a project of this scale.

In larger-scale applications or cases where inputs are more varied, dynamic calculation would likely be the preferred approach for better scalability and flexibility. However, for this project's scope and goals, precalculation was the "good enough" solution.

In [15]:
# Perform an inner join on our cost_of_living_data_clipped and the GeoDataFrame
complete_gdf = cost_of_living_data_clipped.merge(gdf_clipped, how='inner', 
            left_on=cost_of_living_data_clipped['county_fip_last_three_digits'], right_on=gdf_clipped['COUNTYFP'].astype('Int64'))

In [16]:
complete_gdf.describe()

key_0     case_id   county_fips       Housing          Food  \
count  790.000000  790.000000    790.000000    790.000000    790.000000   
mean    66.759494  354.392405  12066.759494  15383.939241  11014.587342   
std     37.727666   19.019314     37.727666   5434.746848   4337.059179   
min      1.000000  322.000000  12001.000000   7128.000000   3540.000000   
25%     37.000000  339.000000  12037.000000  11034.000000   7770.000000   
50%     65.000000  353.000000  12065.000000  13956.000000  10644.000000   
75%     99.000000  371.000000  12099.000000  18828.000000  14073.000000   
max    133.000000  388.000000  12133.000000  30984.000000  23400.000000   

       Transportation    Healthcare  Other Necessities      Childcare  \
count      790.000000    790.000000          790.000000    790.000000   
mean     17170.891139  15275.939241         9346.769620  10371.918987   
std       2475.287572   5823.641665         3123.057195   6323.711868   
min      10416.000000   4980.000000         3864.000000      0.000000   
25%      15600.000000  11085.000000         6831.000000   6273.000000   
50%      17454.000000  14982.000000         9030.000000  12432.000000   
75%      18912.000000  19305.000000        11292.000000  15165.000000   
max      22728.000000  34236.000000        19200.000000  21168.000000   

              Taxes  ...  num_counties_in_st  st_cost_rank  st_med_aff_rank  \
count    790.000000  ...               790.0    790.000000       790.000000   
mean    9584.111392  ...                67.0     34.316456        33.430380   
std     3608.651987  ...                 0.0     19.270961        19.427603   
min     4968.000000  ...                67.0      1.000000         1.000000   
25%     6927.000000  ...                67.0     18.000000        16.000000   
50%     8520.000000  ...                67.0     34.000000        33.000000   
75%    11496.000000  ...                67.0     51.000000        50.000000   
max    25284.000000  ...                67.0     67.000000        67.000000   

       st_income_rank  Total_minus_Transport  Transportation_base  \
count      790.000000             790.000000           790.000000   
mean        34.544304           70977.615190          4292.722785   
std         19.381303           24848.617266           618.821893   
min          1.000000           25572.000000          2604.000000   
25%         18.000000           51651.000000          3900.000000   
50%         34.000000           71010.000000          4363.500000   
75%         52.000000           88251.000000          4728.000000   
max         67.000000          150780.000000          5682.000000   

       Transportation_per_day  county_fip_last_three_digits         ALAND  \
count              790.000000                    790.000000  7.900000e+02   
mean              2575.633671                     66.759494  2.051173e+09   
std                371.293136                     37.727666  9.584108e+08   
min               1562.400000                      1.000000  6.308045e+08   
25%               2340.000000                     37.000000  1.442996e+09   
50%               2618.100000                     65.000000  1.783430e+09   
75%               2836.800000                     99.000000  2.466005e+09   
max               3409.200000                    133.000000  5.171811e+09   

             AWATER  
count  7.900000e+02  
mean   6.036829e+08  
std    1.306775e+09  
min    8.095870e+05  
25%    2.330328e+07  
50%    2.601475e+08  
75%    8.041112e+08  
max    1.115386e+10  

[8 rows x 22 columns]

In [17]:
import numpy as np
# Step 1: Create the income range
income_levels = np.arange(0, 210000, 10000)  # From 0 to 200,000 in 10k increments

Another legacy of the app idea is precomputing our colors. Each ratio resolves to a hex code to show red, orange, yellow, or green for an Income/cost of living ratio. If you make more than 1.25 times the cost of an area, it's green, and it descends from there.

In [18]:
# Step 2: Expand the data
expanded_data = pd.DataFrame(np.repeat(complete_gdf.values, len(income_levels), axis=0), columns=complete_gdf.columns)
expanded_data['Income'] = np.tile(income_levels, len(complete_gdf))
expanded_data['Income'] = pd.to_numeric(expanded_data['Income'])

expanded_data['Income_minus_Total'] = expanded_data['Income'] - expanded_data['Total']
expanded_data['Income_Total_Ratio'] = expanded_data['Income'] / expanded_data['Total']
expanded_data['Median_minus_Total'] = expanded_data['median_family_income'] - expanded_data['Total']
expanded_data['Median_Total_Ratio'] = expanded_data['median_family_income'] / expanded_data['Total']

# Function to assign colors based on Income/Cost of Living Ratio
def get_color(ratio):
    if ratio < 0.8:
        return "#e74c3c"
    elif 0.8 <= ratio < 1.0:
        return "#f39c12"
    elif 1.0 <= ratio < 1.25:
        return "#f1c40f"
    else:
        return "#27ae60"

expanded_data['color_income'] = expanded_data['Income_Total_Ratio'].apply(get_color)
expanded_data['color_median'] = expanded_data['Median_Total_Ratio'].apply(get_color)
expanded_data = gpd.GeoDataFrame(expanded_data, geometry='geometry')

### GIS and CRS

Geographic Information Systems (GIS) and Coordinate Reference Systems (CRS) are fascinating technologies I had to become acquainted with over the course of this work. Writing about either in depth is outside the scope of my knowledge and this project, but, to keep it short, there are many considerations to take into account when you're trying to draw over a map of a place. Are you projecting on to a flat map? A 3D depiction of the Earth? Are you focused on a specific locality? Are geological features important or country borders? 

The geometry column in our data assumes we are using what's called the World Geodetic System 1984 (WGS84), it's widely used in mapping and surveying applications and is the reference system used by GPS. The CRS used for WGS84 is the European Petroleum Survey Group (EPSG) code 4326. Without specifying the correct EPSG code for our purposes our county lines are more likely to end up in the middle of the Atlantic Ocean.

Spatial Data: https://spatialreference.org/ref/epsg/

In [19]:
# Convert MultiLineString to Polygon where possible
expanded_data['geometry'] = expanded_data['geometry'].apply(lambda geom: geom.convex_hull if geom.geom_type == 'MultiLineString' else geom)
# CRS for displaying accurately with folium
expanded_data.crs= "EPSG:4326"

### To Summarize

We have two datasets we have examined, cleaned, and put together; one gives cost of living data for the counties we will be looking at and the second gives the location and shapes of those counties.

Using folium we are going to put it all together: We will have a function that takes an income level and family type, and give back a map with color coding to show the Income/cost-of-living ratio. Included in the tooltip is other relevant information that might be useful, such as median income in the county for that family type.

In [20]:
import folium
def create_map(data, income, family):

    filtered_gdf = data[
    (data['Income'].astype(int) == int(income)) &
    (data['Family'].str.strip().str.lower() == family.strip().lower())].copy()
    
    m = folium.Map(location=[27.8, -81.7], zoom_start=6.5, tiles="cartodbpositron")

    # This assumes your GeoDataFrame is already filtered by family size + income
    # and has a 'color_income' column, and your geometries are valid.
    
    folium.GeoJson(
        filtered_gdf,  # your GeoDataFrame
        name="counties",
        style_function=lambda feature: {
            "fillColor": feature["properties"]["color_income"],
            "color": "black",  # border color
            "weight": 0.2,
            "fillOpacity": 0.2,
        },
        tooltip=folium.GeoJsonTooltip(
            fields=["County", "Income_Total_Ratio", "Income","Total","median_family_income","Family"],
            aliases=["County", "Income to COL Ratio","Income","Cost-of-Living","Median Income","Family",],
            localize=True
        ),
    ).add_to(m)
    
    folium.LayerControl().add_to(m)
    
    return m

## **7 Creating our map**

With the create_map function you can adjust the last two variables to get a map based on your specific income or family size. The ranges of income are \\\$0 to \\$200,000 in \\$10,000 increments (it only takes 50,000, 60,000 etc.). 

You may also specify your family type from the 1 person with no children (1p0c) to up to two adults with four children (2p4c).

The tooltip will give you the name of the county, your Income/cost of living ratio (which corresponds to the county color), the Income you entered, the cost of living for that county for a family of the same size, the median income for that county for a family of the same size, and the family size you entered.

📌 NOTE: If the map doesn't display, click Edit>Clear Output of All Cells then Run>Run All Cells. Binder opens the notebook in a "not trusted" state, so interactive content may not appear until re-executed.

In [21]:
# creating a map for a  family of four with income of $100,000
create_map(expanded_data,100000,'2p2c')